# **Import and Clean WarFlight DataSet**

In [2]:
# import dataset

import pandas as pd
wd = pd.read_csv ('./Missoula-Warflight.csv', delimiter = ',')  # read warflight csv file into Pandas dataframe

print("Total WiFi AP entries: " + str(len(wd)))
wd.sample(10)  # 10 random networks

Total WiFi AP entries: 5293


MAC                           SSID  ... AccuracyMeters  Type
1253  A8:9A:93:A2:2E:8E            MySpectrumWiFi88-2G  ...            243  WIFI
2694  C6:41:1E:BF:E2:8F                 RedDwarf-guest  ...            220  WIFI
101   2A:E8:29:5A:1B:8C  Missoula Paddleheads  - Guest  ...            291  WIFI
2419  1A:E8:29:14:23:36               Logjam - private  ...            159  WIFI
3841  B0:7F:B9:A1:D3:D7            MySpectrumWiFid8-2G  ...            160  WIFI
2892  02:6A:E3:65:BC:8F                       Sunshine  ...            221  WIFI
2525  10:DA:43:80:A3:D1                          Citi2  ...            159  WIFI
3664  38:35:FB:95:78:FE                        HOTR-2G  ...            160  WIFI
2257  00:5F:67:72:E3:39                   Pixiegarden1  ...            159  WIFI
14    FE:EC:DA:97:BE:69               Poverello Center  ...            290  WIFI

[10 rows x 11 columns]

In [3]:
# clean dataset by dropping excessive data entries

wd.drop(wd.index[wd["FirstSeen"] <= "2021-8-21 18:43:25"],0, inplace=True) # before takeoff
wd.drop(wd.index[wd["FirstSeen"] >= "2021-8-21 18:46:58"],0, inplace=True) # after landing

print("Total WiFi AP entries: " + str(len(wd)))

Total WiFi AP entries: 1938


# **Map All Data Entries + WarFlying Route**

In [25]:
# plot all network entries as a cluster map w/ warflight route

import folium
from folium import FeatureGroup, LayerControl, Map, Marker
from folium.plugins import MarkerCluster

MarkerCluster()

# autofit map boundaries from dataset
net_map = folium.Map(wd[['Latitude', 'Longitude']].mean().values.tolist())
net_map.fit_bounds([wd[['Latitude', 'Longitude']].min().values.tolist(), wd[['Latitude', 'Longitude']].max().values.tolist()])
network_cluster = MarkerCluster().add_to(net_map)

networks = wd.values

# warflight route
folium.PolyLine(wd[['Latitude', 'Longitude']].values.tolist(),line_opacity = 0.5, weight = 4).add_to(net_map)

# cluster map of all network entries
for network in networks: folium.Marker([network[6],network[7]], popup=network[1], icon=folium.Icon(color='darkblue', icon_color='white', icon='wifi', angle=0, prefix='fa')).add_to(network_cluster)

# first and last data entry
folium.Marker([networks[0][6], networks[0][7]], popup=networks[0][3], icon=folium.Icon(color='green', icon_color='white', icon='plane', angle=0, prefix='fa')).add_to(net_map)
folium.Marker([networks[len(networks)-1][6],networks[len(networks)-1][7]], popup= networks[len(networks)-1][3], icon=folium.Icon(color='red', icon_color='white', icon='plane', angle=0, prefix='fa')).add_to(net_map)

display(net_map)

# **Known Devices + Network HeatMap**

In [8]:
# network concentration heat map + known device location

known_devices = ["Target3", "Bingus Mobile"]

import folium, numpy
from folium import Map, Marker, plugins

# autofit map boundaries from dataset
wd_heat_map = folium.Map(wd[['Latitude', 'Longitude']].mean().values.tolist())
wd_heat_map.fit_bounds([wd[['Latitude', 'Longitude']].min().values.tolist(), wd[['Latitude', 'Longitude']].max().values.tolist()])

for device in wd.loc[wd["SSID"].isin(known_devices)].values:
  folium.Marker( location=[device[6], device[7]], popup=device[1], icon=folium.Icon(color="darkblue",icon='wifi',prefix='fa')).add_to(wd_heat_map)

wd_heat_map.add_child(plugins.HeatMap(wd[['Latitude', 'Longitude']].to_numpy(), radius=30))
display(wd_heat_map)

# **Network Encryption Cluster**

In [24]:
import folium
from folium import FeatureGroup, LayerControl, Map, Marker
from folium.plugins import MarkerCluster


myMap = folium.Map(wd[['Latitude', 'Longitude']].mean().values.tolist())
myMap.fit_bounds([wd[['Latitude', 'Longitude']].min().values.tolist(), wd[['Latitude', 'Longitude']].max().values.tolist()])

MarkerCluster()

# map feature groups for different encryption types
wep_feature_group = folium.FeatureGroup("WEP")
wpa_feature_group = folium.FeatureGroup("WPA")
wpa2_feature_group = folium.FeatureGroup("WPA2")
opn_feature_group = folium.FeatureGroup("Open")
none_feature_group = folium.FeatureGroup("None")

networks = wd.values

# add network coordinates
for network in networks:
  if   (network[2] == "[WPA-PSK-CCMP+TKIP][ESS]"):
    folium.Marker(location=[network[6],network[7]],  popup=network[1], icon=folium.Icon(color="blue",icon='user-secret',prefix='fa')).add_to(wpa_feature_group)

  elif (network[2] == "[WPA2-PSK-CCMP+TKIP][ESS]"):
    folium.Marker(location=[network[6],network[7]],  popup=network[1], icon=folium.Icon(color="green",icon='user-secret',prefix='fa')).add_to(wpa2_feature_group)

  elif (network[2] == "[WEP][ESS]"):
    folium.Marker(location=[network[6],network[7]],  popup=network[1], icon=folium.Icon(color="red",icon='user-secret',prefix='fa')).add_to(wep_feature_group)

  elif (network[2] == "[ESS]"):
    folium.Marker(location=[network[6],network[7]],  popup=network[1], icon=folium.Icon(color="orange",icon='user-secret',prefix='fa')).add_to(opn_feature_group)

  elif (network[2] == "[WPA-PSK-CCMP+TKIP][WPA2-PSK-CCMP+TKIP][ESS]"):
    folium.Marker(location=[network[6],network[7]],  popup=network[1], icon=folium.Icon(color="purple",icon='user-secret',prefix='fa')).add_to(none_feature_group)


wep_feature_group.add_to(myMap)
wpa_feature_group.add_to(myMap)
wpa2_feature_group.add_to(myMap)
opn_feature_group.add_to(myMap)
none_feature_group.add_to(myMap)

folium.LayerControl().add_to(myMap)

display(myMap)